PRIMERO PREPARAMOS TODAS NUESTRAS FUNCIONES PARA PODER SER CONVOCADAS LUEGO.

Instalamos 

In [1]:
%pip install qdrant-client transformers torch langchain pymupdf

  Obtaining dependency information for qdrant-client from https://files.pythonhosted.org/packages/e4/52/f49b0aa96253010f57cf80315edecec4f469e7a39c1ed92bf727fa290e57/qdrant_client-1.14.2-py3-none-any.whl.metadata
  Obtaining dependency information for pymupdf from https://files.pythonhosted.org/packages/71/c2/a9059607f80dcaf2392f991748cfc53456820392c0220cff02572653512a/pymupdf-1.25.5-cp39-abi3-win_amd64.whl.metadata
  Obtaining dependency information for grpcio>=1.41.0 from https://files.pythonhosted.org/packages/ee/3f/cf92e7e62ccb8dbdf977499547dfc27133124d6467d3a7d23775bcecb0f9/grpcio-1.71.0-cp311-cp311-win_amd64.whl.metadata
  Using cached grpcio-1.71.0-cp311-cp311-win_amd64.whl.metadata (4.0 kB)
  Obtaining dependency information for portalocker<3.0.0,>=2.7.0 from https://files.pythonhosted.org/packages/9b/fb/a70a4214956182e0d7a9099ab17d50bfcba1056188e9b14f35b9e2b62a0d/portalocker-2.10.1-py3-none-any.whl.metadata
  Using cached portalocker-2.10.1-py3-none-any.whl.metadata (8.5 kB)
  


[notice] A new release of pip is available: 23.2.1 -> 25.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Importamos librerias

In [19]:
from sentence_transformers import SentenceTransformer
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.schema import Document
from qdrant_client import QdrantClient
from qdrant_client.models import PointStruct, Distance, VectorParams
import fitz  # PyMuPDF

Definimos funciones
1) Cargar los pdf por sus bloques de paginas

In [20]:
def pdfachunk(path, chunk_size_pages=20):
    doc = fitz.open(path)
    chunks = []
    for i in range(0, len(doc), chunk_size_pages):
        text = ""
        for page_num in range(i, min(i + chunk_size_pages, len(doc))):
            text += doc[page_num].get_text()
        chunks.append(text)
    doc.close()
    return chunks

2) Dividir texto en chunks más pequeños con solapamiento

In [21]:
def split_chunks(raw_chunks, chunk_size=1024, chunk_overlap=100):
    docs = [Document(page_content=chunk) for chunk in raw_chunks]
    splitter = RecursiveCharacterTextSplitter(
        chunk_size=chunk_size,
        chunk_overlap=chunk_overlap,
        separators=["\n\n", "\n", ".", " "]
    )
    return splitter.split_documents(docs)

3) Generar embeddings en batch

In [22]:
def generaremben(model, texts):
    texts = [t for t in texts if t.strip()]  # filtra vacíos
    if not texts:
        raise ValueError("No hay textos válidos para generar embeddings.")
    return model.encode(texts, batch_size=16, show_progress_bar=True)


4) Insertar los docemtos en QDRANT localemente

In [23]:
def insertarenqdra(embeddings, texts, collection_name="pdf_chunks"):
    client = QdrantClient(path="./qdrant_data")  # persistente

    dim = len(embeddings[0])
    client.recreate_collection(
        collection_name=collection_name,
        vectors_config=VectorParams(size=dim, distance=Distance.COSINE)
    )

    points = [
        PointStruct(id=i, vector=embeddings[i].tolist(), payload={"text": texts[i]})
        for i in range(len(embeddings))
    ]

    client.upsert(collection_name=collection_name, points=points)
    print(f"✅ Insertados {len(points)} vectores en Qdrant.")

5) Funcion modelo para no cargarlo siempre

In [6]:
def load_nv_model():
    return AutoModel.from_pretrained("nvidia/NV-Embed-v2", trust_remote_code=True)

Probamos

In [24]:
pdf_path="./DOCS/Decreto-Supremo-N_-018-2019-JUS.pdf" 

In [25]:
pdf_chunks = pdfachunk(pdf_path)

In [26]:
split_docs = split_chunks(pdf_chunks)

In [27]:
texts = [doc.page_content for doc in split_docs]

Definimos nuestro modelo de embbending

NECESITAMOS DATASETS Y EINOPS

In [ ]:
%pip install datasets einops

In [28]:
model = SentenceTransformer("all-MiniLM-L6-v2")

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


In [13]:
print(type(model))

<class 'transformers_modules.nvidia.NV-Embed-v2.c50d55f43bde7e6a18e0eaa15a62fd63a930f1a1.modeling_nvembed.NVEmbedModel'>


In [29]:
embeddings = generaremben(model, texts)

Batches: 100%|██████████| 12/12 [00:03<00:00,  3.29it/s]


In [30]:
insertarenqdra(embeddings, texts, collection_name="jus_decreto_018")

C:\Users\adm\AppData\Local\Temp\ipykernel_26272\752761030.py:5: DeprecationWarning: `recreate_collection` method is deprecated and will be removed in the future. Use `collection_exists` to check collection existence and `create_collection` instead.
  client.recreate_collection(


✅ Insertados 181 vectores en Qdrant.


Funcion para consultar con qdrant

In [31]:
from qdrant_client import QdrantClient
import numpy as np

In [ ]:
def query_qdrant(query, model, collection_name, top_k=5):
    # Generar embedding de la consulta
    query_embedding = model.encode([query])[0]
    
    # Conexión al cliente Qdrant
    client = QdrantClient(path="./qdrant_data")

    # Realizar búsqueda en la colección
    results = client.search(
        collection_name=collection_name,
        query_vector=query_embedding.tolist(),
        limit=top_k,  # Limitar a los primeros K resultados más similares
        with_payload=True  # Incluir el texto en los resultados
    )

    return results

In [36]:
query = "¿Cuál es el propósito de la Ley 018-2019?"
results = query_qdrant(query, model,"jus_decreto_018")

RuntimeError: Storage folder ./qdrant_data is already accessed by another instance of Qdrant client. If you require concurrent access, use Qdrant server instead.